### Perguntas
- Pergunta principal: Qual é a diferença de uso das bicicletas pelos **clientes casuais e anuais (membros)**?
- Perguntas específicas:
> - Qual é a média de duração da locação das bicicletas?
> - Quais são os dias da semana com a maior/menor quantidade de locações?
> - Qual é o total de clientes por dia, mês e ano?
> - Quais são os tipos de bicicleta mais alugados?
> - Quais são as estações mais utilizadas?
> - Qual é a localização geográfica das retiradas e devoluções?
> - Quais são os horários do dia com maiores locações e devoluções?

### Upload dos dados (.csv)
- Todos os arquivos (datasets) foram carregados para um volume dentro do banco de dados (portfolio_citybikes)
- Posteriormente, foram criadas tabelas em lotes de 10 em 10 de maneira manual através da interface do Databricks (/Volumes/)
- A tabela com o modelo de esquema foi criada inicialmente a partir do arquivo "divvy_trips_2020_q_1.csv"

In [0]:
-- Criação da tabela modelo com dados iniciais e alteração de alguns tipos de dados
-- Esta tabela será a base para a tabela fonte com todos os dados consolidados (jan2020 até jul2025)
CREATE TABLE workspace.portfolio_citybikes.tabela_fonte_consolidada AS
SELECT
  ride_id,
  rideable_type,
  started_at,
  ended_at,
  start_station_name,
  CAST(start_station_id AS STRING),
  end_station_name,
  CAST(end_station_id AS STRING),
  start_lat,
  start_lng,
  end_lat,
  end_lng,
  member_casual,
  _rescued_data
  FROM workspace.portfolio_citybikes.divvy_trips_2020_q_1

### Adição de dados na tabela modelo

In [0]:
-- Inclusão de dados na tabela fonte (abr2020 até jan2021)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202004_202101

num_affected_rows num_inserted_rows 3211630 3211630

In [0]:
-- Inclusão de dados na tabela fonte (fev2021 até nov2021)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202102_202111

num_affected_rows num_inserted_rows 5250689 5250689

In [0]:
-- Inclusão de dados na tabela fonte (dez2021 até set2022)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202112_202209

num_affected_rows num_inserted_rows 4837031 4837031

In [0]:
-- Inclusão de dados na tabela fonte (out2022 até jul2023)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202210_202307

num_affected_rows num_inserted_rows 4236335 4236335

In [0]:
-- Inclusão de dados na tabela fonte (ago2023 até mai2024)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202308_202405

num_affected_rows num_inserted_rows 4256010 4256010

In [0]:
-- Inclusão de dados na tabela fonte (jun2024 até mar2025)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202406_202503

num_affected_rows num_inserted_rows 4755050 4755050

In [0]:
-- Inclusão de dados na tabela fonte (abr2025 até jul2025)
INSERT INTO workspace.portfolio_citybikes.tabela_fonte_consolidada
TABLE workspace.portfolio_citybikes.202504_202507

num_affected_rows num_inserted_rows 2316133 2316133

### Verificação de linhas
Verificação da quantidade original de linhas e posteriormente à execução do comando INSERT INTO para a tabela_fonte_consolidada

In [0]:
-- Garantindo que não existe nenhum valor nulo na coluna ride_id
SELECT ride_id
FROM workspace.portfolio_citybikes.tabela_fonte_consolidada
WHERE ride_id IS NULL

ride_id

In [0]:
-- Contagem do total de linhas da tabela fonte consolidada (verificação)
SELECT COUNT(ride_id)
FROM workspace.portfolio_citybikes.tabela_fonte_consolidada

COUNT(ride_id) 29289765

In [0]:
-- Contagem total utilizando CTE para verificação
WITH contagem_linhas AS (
  SELECT ride_id
  FROM workspace.portfolio_citybikes.divvy_trips_2020_q_1
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202004_202101
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202102_202111
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202112_202209
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202210_202307
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202308_202405
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202406_202503
  UNION ALL
  SELECT ride_id
  FROM workspace.portfolio_citybikes.202504_202507
)
SELECT COUNT(ride_id)
FROM contagem_linhas

COUNT(ride_id) 29289765

### Modelagem SQL
- fact_rides
> - ride_id
> - start_lat
> - start_lng
> - end_lat
> - end_lng
> - started_at
> - ended_at
> - start_station_fk
> - end_station_fk
> - duracao_locacao: coluna calculada (started_at - ended_at)
> - dia_semana_retirada: coluna calculada (WEEKDAY)
> - dia_semana_devolucao: coluna calculada (WEEKDAY)
> - hora_retirada: coluna calculada (HOUR)
> - hora_devolucao: coluna calculada (HOUR)
> - rideable_type_fk
> - member_casual_fk
- dim_rideable_type
- dim_start_station
- dim_end_station
- dim_member_casual

In [0]:
-- Criação de tabela de dimensão (tipo de bicicleta)
CREATE OR REPLACE TABLE workspace.portfolio_citybikes.dim_rideable_type AS
SELECT
  ROW_NUMBER() OVER (ORDER BY rideable_type) AS id_rideable_type,
  rideable_type
FROM
  (SELECT DISTINCT rideable_type FROM workspace.portfolio_citybikes.tabela_fonte_consolidada)

num_affected_rows num_inserted_rows

In [0]:
-- Verificação da tabela criada
SELECT *
FROM workspace.portfolio_citybikes.dim_rideable_type

id_rideable_type rideable_type 1 classic_bike 2 docked_bike 3 electric_bike 4 electric_scooter

In [0]:
-- Verificação do data_type da tabela criada
DESCRIBE TABLE workspace.portfolio_citybikes.dim_rideable_type

col_name data_type comment id_rideable_type int null rideable_type string null

In [0]:
-- Criação de tabela de dimensão (estação inicial)
CREATE OR REPLACE TABLE workspace.portfolio_citybikes.dim_start_station AS
SELECT
  ROW_NUMBER() OVER (ORDER BY start_station_name) AS start_station_id,
  start_station_name
FROM (SELECT DISTINCT start_station_name FROM workspace.portfolio_citybikes.tabela_fonte_consolidada)
WHERE
  start_station_name IS NOT NULL

num_affected_rows num_inserted_rows

In [0]:
-- Verificação da tabela criada
SELECT *
FROM workspace.portfolio_citybikes.dim_start_station

start_station_id start_station_name 1 10101 S Stony Island Ave 2 111th St - Morgan Park Metra 3 2112 W Peterson Ave 4 21st St & Pulaski Rd 5 351 6 410 7 532 E 43rd St 8 63rd & Western Ave - north corner 9 63rd & Western Ave - south corner 10 63rd St Beach 11 83rd St (Avalon Park) Metra 12 900 W Harrison St 13 Abbott Park 14 Aberdeen St & 103rd St 15 Aberdeen St & Carroll Ave 16 Aberdeen St & Jackson Blvd 17 Aberdeen St & Monroe St 18 Aberdeen St & Randolph St 19 Ada St & 113th Place 20 Ada St & 113th St 21 Ada St & 117th St 22 Ada St & 119th St 23 Ada St & 79th St 24 Ada St & 95th St 25 Ada St & Washington Blvd 26 Addison Red Line 27 Addison Red Line Corral 28 Addison/Racine 29 Addison/Racine Corral 30 Addison/Sheffield SE Corral 31 Addison/Sheffield SW Corral 32 Addison/Wilton Corral 33 Adler Planetarium 34 Al Raby School 35 Albany Ave & 103rd St 36 Albany Ave & 111th St - NW 37 Albany Ave & 16th St 38 Albany Ave & 26th St 39 Albany Ave & 63rd St 40 Albany Ave & Belmont Ave 41 Albany Ave & Bloomingdale Ave 42 Albany Ave & Douglas Blvd 43 Albany Ave & Montrose Ave 44 Altgeld Gardens 45 Archer & Wentworth 46 Archer (Damen) Ave & 37th St 47 Archer Ave & 43rd St 48 Archer Ave & 49th St 49 Archer Ave & Homan Ave 50 Archer Ave & Wentworth Ave 51 Archer Park 52 Artesian Ave & 55th St 53 Artesian Ave & 71st St 54 Artesian Ave & Hubbard St 55 Artesian Ave & Marquette Rd 56 Ashland Ave & 13th St 57 Ashland Ave & 45th St 58 Ashland Ave & 45th St - midblock south 59 Ashland Ave & 46th St 60 Ashland Ave & 50th St 61 Ashland Ave & 63rd St 62 Ashland Ave & 66th St 63 Ashland Ave & 69th St 64 Ashland Ave & 71st St 65 Ashland Ave & 73rd St 66 Ashland Ave & 74th St 67 Ashland Ave & 76th St 68 Ashland Ave & 78th St 69 Ashland Ave & Archer Ave 70 Ashland Ave & Augusta Blvd 71 Ashland Ave & Belle Plaine Ave 72 Ashland Ave & Blackhawk St 73 Ashland Ave & Chicago Ave 74 Ashland Ave & Division St 75 Ashland Ave & Garfield Blvd 76 Ashland Ave & Grace St 77 Ashland Ave & Grand Ave 78 Ashland Ave & Lake St 79 Ashland Ave & McDowell Ave 80 Ashland Ave & Pershing Rd 81 Ashland Ave & Wellington Ave 82 Ashland Ave & Wrightwood Ave 83 Augusta Blvd & Laramie Ave 84 Austin Ave & Milwaukee Ave 85 Austin Ave & Roscoe St 86 Austin Ave & Wellington Ave - midblock 87 Austin Ave & Wrightwood Ave 88 Austin Blvd & Chicago Ave 89 Austin Blvd & Lake St 90 Austin Blvd & Madison St 91 Austin Blvd & North Ave 92 Austin Branch Chicago Public Library 93 Ave L & 114th 94 Avenue J & 102nd St 95 Avenue J & 106th St 96 Avenue J & 112th St 97 Avenue L & 114th St 98 Avenue M & 132nd St 99 Avenue O & 118th St 100 Avenue O & 134th St 101 Avers Ave & 16th St 102 Avers Ave & Archer Ave 103 Avers Ave & Belmont Ave 104 Avers Ave & Foster Ave 105 Avers Ave & Irving Park Rd 106 Avers Ave & Ogden Ave 107 Avondale Ave & Addison St 108 Avondale Ave & Irving Park Rd 109 Back of the Yards Park 110 Baltimore Ave & 132nd St 111 Baltimore Ave & 133rd St 112 Baltimore Ave & 87th St 113 Base - 2132 W Hubbard 114 Base - 2132 W Hubbard Warehouse 115 Bell Ave & 95th St 116 Bennett Ave & 79th St 117 Bennett Ave & 96th St 118 Bensley Ave & 103rd St 119 Benson Ave & Church St 120 Bernard St & Elston Ave 121 Bernard St & Peterson Ave 122 Big Marsh Park 123 Bishop St & 46th St 124 Bissell St & Armitage Ave 125 Bissell St & Armitage Ave - Charging 126 Bissell St & Armitage Ave* 127 Blackstone Ave & 59th St 128 Blackstone Ave & Hyde Park Blvd 129 Bloomingdale Ave & Harlem Ave 130 Blue Island Ave & 18th St 131 Bosworth Ave & Howard St 132 Bradley Park 133 Brandon Ave & 91st St 134 Brighton Park Branch Chicago Library 135 Broadway & Argyle St 136 Broadway & Barry Ave 137 Broadway & Belmont Ave 138 Broadway & Berwyn Ave 139 Broadway & Cornelia Ave 140 Broadway & Granville Ave 141 Broadway & Oakdale Ave 142 Broadway & Ridge Ave 143 Broadway & Sheridan Rd 144 Broadway & Thorndale Ave 145 Broadway & Waveland Ave 146 Broadway & Wilson - Truman College Vaccination Site 147 Broadway & Wilson Ave 148 Buckingham - Fou

In [0]:
-- Verificação do data_type da tabela criada
DESCRIBE TABLE workspace.portfolio_citybikes.dim_start_station

col_name data_type comment start_station_id int null start_station_name string null

In [0]:
-- Criação de tabela de dimensão (estação final)
CREATE OR REPLACE TABLE workspace.portfolio_citybikes.dim_end_station AS
SELECT
  ROW_NUMBER() OVER (ORDER BY end_station_name) AS end_station_id,
  end_station_name
FROM (SELECT DISTINCT end_station_name FROM workspace.portfolio_citybikes.tabela_fonte_consolidada)
WHERE
  end_station_name IS NOT NULL

num_affected_rows num_inserted_rows

In [0]:
-- Verificação da tabela criada
SELECT *
FROM workspace.portfolio_citybikes.dim_end_station

end_station_id end_station_name 1 10101 S Stony Island Ave 2 111th St - Morgan Park Metra 3 2112 W Peterson Ave 4 21st St & Pulaski Rd 5 410 6 532 E 43rd St 7 63rd & Western Ave - north corner 8 63rd & Western Ave - south corner 9 63rd St Beach 10 83rd St (Avalon Park) Metra 11 900 W Harrison St 12 Abbott Park 13 Aberdeen St & 103rd St 14 Aberdeen St & Carroll Ave 15 Aberdeen St & Jackson Blvd 16 Aberdeen St & Monroe St 17 Aberdeen St & Randolph St 18 Ada St & 113th Place 19 Ada St & 113th St 20 Ada St & 117th St 21 Ada St & 119th St 22 Ada St & 79th St 23 Ada St & 95th St 24 Ada St & Washington Blvd 25 Addison Red Line 26 Addison Red Line Corral 27 Addison/Racine 28 Addison/Racine Corral 29 Addison/Sheffield SE Corral 30 Addison/Sheffield SW Corral 31 Addison/Wilton Corral 32 Adler Planetarium 33 Al Raby School 34 Albany Ave & 103rd St 35 Albany Ave & 111th St - NW 36 Albany Ave & 16th St 37 Albany Ave & 26th St 38 Albany Ave & 63rd St 39 Albany Ave & Belmont Ave 40 Albany Ave & Bloomingdale Ave 41 Albany Ave & Douglas Blvd 42 Albany Ave & Montrose Ave 43 Altgeld Gardens 44 Archer & Wentworth 45 Archer (Damen) Ave & 37th St 46 Archer Ave & 43rd St 47 Archer Ave & 49th St 48 Archer Ave & Homan Ave 49 Archer Ave & Wentworth Ave 50 Archer Park 51 Artesian Ave & 55th St 52 Artesian Ave & 71st St 53 Artesian Ave & Hubbard St 54 Artesian Ave & Marquette Rd 55 Ashland Ave & 13th St 56 Ashland Ave & 45th St 57 Ashland Ave & 45th St - midblock south 58 Ashland Ave & 46th St 59 Ashland Ave & 50th St 60 Ashland Ave & 63rd St 61 Ashland Ave & 66th St 62 Ashland Ave & 69th St 63 Ashland Ave & 71st St 64 Ashland Ave & 73rd St 65 Ashland Ave & 74th St 66 Ashland Ave & 76th St 67 Ashland Ave & 78th St 68 Ashland Ave & Archer Ave 69 Ashland Ave & Augusta Blvd 70 Ashland Ave & Belle Plaine Ave 71 Ashland Ave & Blackhawk St 72 Ashland Ave & Chicago Ave 73 Ashland Ave & Division St 74 Ashland Ave & Garfield Blvd 75 Ashland Ave & Grace St 76 Ashland Ave & Grand Ave 77 Ashland Ave & Lake St 78 Ashland Ave & McDowell Ave 79 Ashland Ave & Pershing Rd 80 Ashland Ave & Wellington Ave 81 Ashland Ave & Wrightwood Ave 82 Augusta Blvd & Laramie Ave 83 Austin Ave & Milwaukee Ave 84 Austin Ave & Roscoe St 85 Austin Ave & Wellington Ave - midblock 86 Austin Ave & Wrightwood Ave 87 Austin Blvd & Chicago Ave 88 Austin Blvd & Lake St 89 Austin Blvd & Madison St 90 Austin Blvd & North Ave 91 Austin Branch Chicago Public Library 92 Ave L & 114th 93 Avenue J & 102nd St 94 Avenue J & 106th St 95 Avenue J & 112th St 96 Avenue L & 114th St 97 Avenue M & 132nd St 98 Avenue O & 118th St 99 Avenue O & 134th St 100 Avers Ave & 16th St 101 Avers Ave & Archer Ave 102 Avers Ave & Belmont Ave 103 Avers Ave & Foster Ave 104 Avers Ave & Irving Park Rd 105 Avers Ave & Ogden Ave 106 Avondale Ave & Addison St 107 Avondale Ave & Irving Park Rd 108 Back of the Yards Park 109 Baltimore Ave & 132nd St 110 Baltimore Ave & 133rd St 111 Baltimore Ave & 87th St 112 Base - 2132 W Hubbard 113 Base - 2132 W Hubbard Warehouse 114 Bell Ave & 95th St 115 Bennett Ave & 79th St 116 Bennett Ave & 96th St 117 Bensley Ave & 103rd St 118 Benson Ave & Church St 119 Bernard St & Elston Ave 120 Bernard St & Peterson Ave 121 Big Marsh Park 122 Bishop St & 46th St 123 Bissell St & Armitage Ave 124 Bissell St & Armitage Ave - Charging 125 Bissell St & Armitage Ave* 126 Blackstone Ave & 59th St 127 Blackstone Ave & Hyde Park Blvd 128 Bloomingdale Ave & Harlem Ave 129 Blue Island Ave & 18th St 130 Bosworth Ave & Howard St 131 Bradley Park 132 Brandon Ave & 91st St 133 Brighton Park Branch Chicago Library 134 Broadway & Argyle St 135 Broadway & Barry Ave 136 Broadway & Belmont Ave 137 Broadway & Berwyn Ave 138 Broadway & Cornelia Ave 139 Broadway & Granville Ave 140 Broadway & Oakdale Ave 141 Broadway & Ridge Ave 142 Broadway & Sheridan Rd 143 Broadway & Thorndale Ave 144 Broadway & Waveland Ave 145 Broadway & Wilson - Truman College Vaccination Site 146 Broadway & Wilson Ave 147 Buckingham - Fountain 148 Bu

In [0]:
-- Verificação do data_type da tabela criada
DESCRIBE TABLE workspace.portfolio_citybikes.dim_end_station

col_name data_type comment end_station_id int null end_station_name string null

In [0]:
-- Criação de tabela de dimensão (tipo de cliente)
CREATE OR REPLACE TABLE workspace.portfolio_citybikes.dim_member_casual AS
SELECT
  ROW_NUMBER() OVER (ORDER BY member_casual) AS id_member_casual,
  member_casual
FROM
  (SELECT DISTINCT member_casual FROM workspace.portfolio_citybikes.tabela_fonte_consolidada)

num_affected_rows num_inserted_rows

In [0]:
-- Verificação da tabela criada (dim_member_casual)
SELECT *
FROM workspace.portfolio_citybikes.dim_member_casual

id_member_casual member_casual 1 casual 2 member

In [0]:
-- Criação da fact table
  CREATE OR REPLACE TABLE workspace.portfolio_citybikes.fact_rides AS
  SELECT
    l.ride_id,
    l.start_lat,
    l.start_lng,
    l.end_lat,
    l.end_lng,
    l.started_at,
    l.ended_at,
    -- Criação da coluna de duração da locação (em segundos)
      TIMESTAMPDIFF(SECOND, l.started_at, l.ended_at) AS duracao_locacao,
    -- Criação da coluna de dia da semana de retirada
      WEEKDAY(l.started_at) AS dia_semana_retirada,
    -- Criação da coluna de dia da semana de devolução
      WEEKDAY(l.ended_at) AS dia_semana_devolucao,
    -- Criação da coluna de hora de retirada
      HOUR(l.started_at) AS hora_retirada,
    -- Criação da coluna de hora de devolução
      HOUR(l.ended_at) AS hora_devolucao,  
    r1.id_rideable_type AS rideable_type_fk,
    r2.id_member_casual AS member_casual_fk,
    r3.start_station_id AS start_station_fk,
    r4.end_station_id AS end_station_fk
  FROM workspace.portfolio_citybikes.tabela_fonte_consolidada AS l
  LEFT JOIN workspace.portfolio_citybikes.dim_rideable_type AS r1
    ON l.rideable_type = r1.rideable_type
  LEFT JOIN workspace.portfolio_citybikes.dim_member_casual AS r2
    ON l.member_casual = r2.member_casual
  LEFT JOIN workspace.portfolio_citybikes.dim_start_station AS r3
    ON l.start_station_name = r3.start_station_name
  LEFT JOIN workspace.portfolio_citybikes.dim_end_station AS r4
    ON l.end_station_name = r4.end_station_name
  -- Excluindo valores negativos da duração da locação, em ocorrências onde ended_at é menor que started_at
    WHERE TIMESTAMPDIFF(SECOND, l.started_at, l.ended_at) > 0

num_affected_rows num_inserted_rows

In [0]:
-- Verificação da tabela criada
SELECT *
FROM workspace.portfolio_citybikes.fact_rides

ride_id start_lat start_lng end_lat end_lng started_at ended_at duracao_locacao dia_semana_retirada dia_semana_devolucao hora_retirada hora_devolucao rideable_type_fk member_casual_fk start_station_fk end_station_fk EACB19130B0CDA4A 41.9665 -87.6884 41.9671 -87.6674 2020-01-21T20:06:59.000Z 2020-01-21T20:14:30.000Z 451 1 1 20 20 2 2 2334 295 8FED874C809DC021 41.9616 -87.666 41.9542 -87.6644 2020-01-30T14:22:39.000Z 2020-01-30T14:26:22.000Z 223 3 3 14 14 2 2 299 2109 789F3C21E472CA96 41.9401 -87.6455 41.9402 -87.653 2020-01-09T19:29:26.000Z 2020-01-09T19:32:17.000Z 171 3 3 19 19 2 2 137 2352 C9A388DAC6ABF313 41.8846 -87.6319 41.8918 -87.6206 2020-01-06T16:17:07.000Z 2020-01-06T16:25:56.000Z 529 0 0 16 16 2 2 302 484 943BC3CBECCFD662 41.8856 -87.6418 41.8899 -87.6343 2020-01-30T08:37:16.000Z 2020-01-30T08:42:48.000Z 332 3 3 8 8 2 2 317 2279 6D9C8A6938165C11 41.8899 -87.6343 41.8846 -87.6446 2020-01-10T12:33:05.000Z 2020-01-10T12:37:54.000Z 289 4 4 12 12 2 2 2276 410 31EB9B8F406D4C82 41.8846 -87.6446 41.8899 -87.6343 2020-01-10T13:07:35.000Z 2020-01-10T13:12:24.000Z 289 4 4 13 13 2 2 411 2279 A2B24E3F9C9720E3 41.8846 -87.6446 41.8899 -87.6343 2020-01-10T07:24:53.000Z 2020-01-10T07:29:50.000Z 297 4 4 7 7 2 2 411 2279 5E3F01E1441730B7 41.8899 -87.6343 41.8846 -87.6446 2020-01-31T16:37:16.000Z 2020-01-31T16:42:11.000Z 295 4 4 16 16 2 2 2276 410 19DC57F7E3140131 41.886 -87.6309 41.8882 -87.6364 2020-01-31T09:39:17.000Z 2020-01-31T09:42:40.000Z 203 4 4 9 9 2 2 295 1124 8639202DD9FD9A41 41.9402 -87.653 41.9445 -87.6547 2020-01-07T22:46:52.000Z 2020-01-07T22:50:08.000Z 196 1 1 22 22 2 2 2349 299 9E74E3BB4FFAB93A 41.8908 -87.6317 41.8834 -87.6412 2020-01-08T16:02:44.000Z 2020-01-08T16:09:04.000Z 380 2 2 16 16 2 2 777 321 3B8B2E2F29B63597 41.8834 -87.6412 41.8908 -87.6317 2020-01-08T09:33:13.000Z 2020-01-08T09:42:02.000Z 529 2 2 9 9 2 2 322 776 0F8517F8D21287D2 41.8834 -87.6412 41.8908 -87.6317 2020-01-23T09:38:11.000Z 2020-01-23T09:45:56.000Z 465 3 3 9 9 2 2 322 776 15A91638FAEC2641 41.9227 -87.6972 41.916 -87.6689 2020-01-28T20:52:50.000Z 2020-01-28T21:09:30.000Z 1000 1 1 20 21 2 2 185 949 E45104F1ED756AF7 41.8777 -87.6353 41.9322 -87.6586 2020-01-07T17:06:14.000Z 2020-01-07T17:42:01.000Z 2147 1 1 17 17 2 2 511 869 219541294624C4B7 41.9324 -87.6527 41.8777 -87.6353 2020-01-07T08:38:55.000Z 2020-01-07T09:11:40.000Z 1965 1 1 8 9 2 2 2350 510 013862D47804B9A4 41.8777 -87.6353 41.9322 -87.6586 2020-01-06T17:16:14.000Z 2020-01-06T17:48:21.000Z 1927 0 0 17 17 2 2 511 869 00678BB4A8438651 41.9322 -87.6586 41.8777 -87.6353 2020-01-06T08:44:31.000Z 2020-01-06T09:21:28.000Z 2217 0 0 8 9 2 2 871 510 A854F81611B5A5C0 41.8892 -87.6385 41.8968 -87.6309 2020-01-19T12:04:10.000Z 2020-01-19T12:10:18.000Z 368 6 6 12 12 2 2 754 286 3479141FF24AD595 41.881 -87.6167 41.884 -87.6247 2020-01-16T17:10:39.000Z 2020-01-16T17:40:40.000Z 1801 3 3 17 17 2 1 799 1008 81D44C3E2353F9BE 41.8793 -87.6399 41.884 -87.6247 2020-01-08T15:47:42.000Z 2020-01-08T15:58:40.000Z 658 2 2 15 15 2 2 210 1008 1AA18F54DC4A8636 41.8679 -87.623 41.8793 -87.6399 2020-01-08T06:29:01.000Z 2020-01-08T06:50:02.000Z 1261 2 2 6 6 2 2 644 208 F5FB29DCF841C9F3 41.9528 -87.65 41.9542 -87.6544 2020-01-08T07:30:59.000Z 2020-01-08T07:33:54.000Z 175 2 2 7 7 2 2 143 2088 869F3755B34163BA 41.8783 -87.6439 41.884 -87.6247 2020-01-23T15:23:54.000Z 2020-01-23T15:37:37.000Z 823 3 3 15 15 2 2 409 1008 00EDF290239E4843 41.8793 -87.6399 41.8783 -87.6439 2020-01-23T14:59:58.000Z 2020-01-23T15:02:49.000Z 171 3 3 14 15 2 2 210 408 CA8E2F8EB7A7639C 41.9029 -87.6873 41.8899 -87.6715 2020-01-11T14:45:48.000Z 2020-01-11T14:58:46.000Z 778 5 5 14 14 2 2 2325 2372 7996062626A55CEF 41.8777 -87.6353 41.8726 -87.6335 2020-01-17T13:44:55.000Z 2020-01-17T13:48:33.000Z 218 4 4 13 13 2 2 511 2282 142E7C9831AE8D5D 41.894 -87.6293 41.8794 -87.6355 2020-01-08T08:23:41.000Z 2020-01-08T08:36:31.000Z 770 2 2 8 8 2 2 405 505 82061D73814586B2 41.8777 -87.6353 41.8819 -87.6488 2020-01-08T16:22:13.000Z 2020-01-08T16:30:43.000Z 510 2 2 

In [0]:
-- Alterando comentário da coluna para informar que a duração da locação está em segundos
ALTER TABLE workspace.portfolio_citybikes.fact_rides
ALTER COLUMN duracao_locacao COMMENT 'Duração da locação em segundos'

In [0]:
-- Verificação do data_type da tabela criada
DESCRIBE TABLE workspace.portfolio_citybikes.fact_rides

col_name data_type comment ride_id string null start_lat double null start_lng double null end_lat double null end_lng double null started_at timestamp null ended_at timestamp null duracao_locacao bigint Duração da locação em segundos dia_semana_retirada int null dia_semana_devolucao int null hora_retirada int null hora_devolucao int null rideable_type_fk int null member_casual_fk int null start_station_fk int null end_station_fk int null